In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)
import numpy as np

# Viz
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

# Feature Engineering
from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import TfidfVectorizer

# Model Storage
from sklearn.externals import joblib

# Metrics
from sklearn.metrics import mean_squared_error

# NN
import keras as k
from keras.models import Sequential
from keras.layers import Dense, Activation

##
from nn import NeuralNetwork
import nn 

Using TensorFlow backend.


In [2]:
train_data = pd.read_csv("/data/project2/train.csv")
test_data = pd.read_csv("/data/project2/test.csv")
print("Train Data Rows: ", len(train_data))
print("Test Data Rows: ", len(test_data))

Train Data Rows:  33235
Test Data Rows:  8309


In [3]:
train_data.head(2)

Index            Region  Total Food Expenditure  \
0  22617               CAR                   81940   
1  21389  V - Bicol Region                   26176   

        Main Source of Income  Agricultural Household indicator  \
0  Enterpreneurial Activities                                 1   
1     Other sources of Income                                 0   

   Bread and Cereals Expenditure  Total Rice Expenditure  Meat Expenditure  \
0                          44171                   40336              9053   
1                          14477                   13067               722   

   Total Fish and  marine products Expenditure  Fruit Expenditure  \
0                                         4499               5245   
1                                         3707                755   

   Vegetables Expenditure  Restaurant and hotels Expenditure  \
0                    6625                               2410   
1                    1560                                260   

   Alcoholic Beverages Expenditure  Tobacco Expenditure  \
0                              145                    0   
1                              280                  235   

   Clothing, Footwear and Other Wear Expenditure  \
0                                           1769   
1                                           1725   

   Housing and water Expenditure  Imputed House Rental Value  \
0                          12300                        3600   
1                           5502                        3600   

   Medical Care Expenditure  Transportation Expenditure  \
0                       544                        2700   
1                       813                         228   

   Communication Expenditure  Education Expenditure  \
0                        636                      0   
1                        138                      0   

   Miscellaneous Goods and Services Expenditure  \
0                                          5466   
1                                          4722   

   Special Occasions Expenditure  Crop Farming and Gardening expenses  \
0                           5150                                22300   
1                              0                                    0   

   Total Income from Entrepreneurial Acitivites Household Head Sex  \
0                                         46100               Male   
1                                          5460               Male   

   Household Head Age Household Head Marital Status  \
0                  63                       Married   
1                  73                       Married   

  Household Head Highest Grade Completed  \
0                    Elementary Graduate   
1                     No Grade Completed   

  Household Head Job or Business Indicator  \
0                        With Job/Business   
1                        With Job/Business   

             Household Head Occupation     Household Head Class of Worker  \
0               Carpenters and joiners   Worked for private establishment   
1  Inland and coastal waters fishermen  Self-employed wihout any employee   

  Type of Household  Total Number of Family members  \
0   Extended Family                               6   
1     Single Family                               2   

   Members with age less than 5 year old  Members with age 5 - 17 years old  \
0                                      2                                  1   
1                                      0                                  0   

   Total number of family members employed Type of Building/House  \
0                                        2           Single house   
1                                        1           Single house   

                                        Type of Roof Type of Walls  \
0  Strong material(galvanized,iron,al,tile,concre...        Strong   
1                 Light material (cogon,nipa,anahaw)         Light   

   House Floor Area  House Age  Number of bedrooms  

In [4]:
numerics = ['object']

newdf = train_data.select_dtypes(include=numerics)
newdf.columns

Index(['Region', 'Main Source of Income', 'Household Head Sex',
       'Household Head Marital Status',
       'Household Head Highest Grade Completed',
       'Household Head Job or Business Indicator', 'Household Head Occupation',
       'Household Head Class of Worker', 'Type of Household',
       'Type of Building/House', 'Type of Roof', 'Type of Walls',
       'Tenure Status', 'Toilet Facilities', 'Main Source of Water Supply'],
      dtype='object')

In [5]:
response_variable = 'Total Household Income'

continuous_vars = ['Total Food Expenditure', 
                   'Bread and Cereals Expenditure', 'Total Rice Expenditure',
                   'Meat Expenditure', 'Total Fish and  marine products Expenditure',
                   'Fruit Expenditure', 'Vegetables Expenditure',
                   'Restaurant and hotels Expenditure', 'Alcoholic Beverages Expenditure',
                   'Tobacco Expenditure', 'Clothing, Footwear and Other Wear Expenditure',
                   'Housing and water Expenditure', 'Imputed House Rental Value',
                   'Medical Care Expenditure', 'Transportation Expenditure','Communication Expenditure', 'Education Expenditure',
                   'Miscellaneous Goods and Services Expenditure', 'Special Occasions Expenditure', 'Crop Farming and Gardening expenses',
                   'Total Income from Entrepreneurial Acitivites', 'House Floor Area']

nominal_vars = ['Agricultural Household indicator', 'Region', 'Main Source of Income', 
                'Household Head Sex','Household Head Marital Status',
                'Household Head Highest Grade Completed',
                'Household Head Job or Business Indicator', 'Household Head Occupation',
                'Household Head Class of Worker', 'Type of Household',
                'Type of Building/House', 'Type of Roof', 'Type of Walls',
                'Tenure Status', 'Toilet Facilities', 'Main Source of Water Supply']

interact_continuous_vars = ['Total Food Expenditure', 'Vegetables Expenditure',
                   'Alcoholic Beverages Expenditure','Tobacco Expenditure',
                   'Housing and water Expenditure', 'Imputed House Rental Value',
                   'Medical Care Expenditure', 'Education Expenditure',
                   'Crop Farming and Gardening expenses',
                   'Total Income from Entrepreneurial Acitivites', 'House Floor Area']

interact_nominal_vars = ['Agricultural Household indicator', 'Main Source of Income', 
                'Household Head Sex','Household Head Marital Status',
                'Household Head Class of Worker',
                'Type of Building/House',
                'Tenure Status']

binary_vars =  ['Electricity']

ordinal_vars = ['Household Head Age','Number of bedrooms','House Age','Number of Television', 'Number of CD/VCD/DVD',
                'Total Number of Family members','Number of Component/Stereo set', 'Number of Refrigerator/Freezer',
                'Number of Washing Machine', 'Number of Airconditioner',
                'Number of Car, Jeep, Van', 'Number of Landline/wireless telephones',
                'Number of Cellular phone', 'Number of Personal Computer',
                'Number of Stove with Oven/Gas Range', 'Number of Motorized Banca',
                'Number of Motorcycle/Tricycle','Members with age less than 5 year old','Members with age 5 - 17 years old','Total number of family members employed'] 

In [6]:
#Split the columns into continuous, categorical
train_continuous = train_data[continuous_vars]
train_categorical = train_data[nominal_vars + binary_vars]
train_ordinal = train_data[ordinal_vars]
train_y = train_data[response_variable]

test_continuous = test_data[continuous_vars]
test_categorical = test_data[nominal_vars + binary_vars]
test_ordinal = test_data[ordinal_vars]


print('Continuous Set has ' + str(len(train_continuous.columns)) + ' columns')
print('Categorical Set has ' + str(len(train_categorical.columns)) + ' columns')
print('Ordinal Set has ' + str(len(train_ordinal.columns)) + ' columns')

Continuous Set has 22 columns
Categorical Set has 17 columns
Ordinal Set has 20 columns


### Continuous Variables Neural Network

In [7]:
# Scale the continuous variables
xScaler = StandardScaler()
train_continuous_scaled = pd.DataFrame(xScaler.fit_transform(train_continuous), columns=continuous_vars)
test_continuous_scaled = pd.DataFrame(xScaler.transform(test_continuous), columns=continuous_vars)

yScaler = StandardScaler()
train_y_scaled = pd.DataFrame(yScaler.fit_transform(train_y))

/opt/conda/lib/python3.5/site-packages/sklearn/utils/validation.py:429: DataConversionWarning: Data with input dtype int64 was converted to float64 by StandardScaler.
  warnings.warn(msg, _DataConversionWarning)
/opt/conda/lib/python3.5/site-packages/sklearn/preprocessing/data.py:586: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/opt/conda/lib/python3.5/site-packages/sklearn/preprocessing/data.py:649: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)


In [8]:
# Configure the Neural Network
nn = NeuralNetwork(len(train_continuous_scaled.columns))
nn.add_layer(30, "tanh").add_layer(1, "identity", bias = False)

In [9]:
# Train the Neural Network
nn.fit(train_continuous_scaled.astype(float).as_matrix(), pd.DataFrame(train_y_scaled).astype(float).as_matrix(), eta = 0.0001, epochs = 10)

Inputs have been converted. Training starting now.
Epoch 0 - Training cost: 2.1736476164
Epoch 0 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 1 - Training cost: 0.465036932429
Epoch 1 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 2 - Training cost: 0.432707927494
Epoch 2 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 3 - Training cost: 0.414283786955
Epoch 3 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 4 - Training cost: 0.399389941725
Epoch 4 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 5 - Training cost: 0.386452322158
Epoch 5 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0

In [10]:
# Predict with the Neural Network against training data for metrics purposes
predicted_y_scaled = nn.predict(train_continuous_scaled)
predicted_y = yScaler.inverse_transform(predicted_y_scaled.reshape(predicted_y_scaled.shape[0],))
mean_squared_error(train_y_scaled, predicted_y_scaled)

0.33746772125682845

In [11]:
# Predict with the Neural Network against test data
predicted_y_scaled_test = nn.predict(test_continuous_scaled)
predicted_y_test = yScaler.inverse_transform(predicted_y_scaled_test.reshape(predicted_y_scaled_test.shape[0],))

### Categorical Variable Neural Network

In [13]:
train_categorical_dummied = dummyify(train_categorical, nominal_vars)
test_categorical_dummied = dummyify(test_categorical, nominal_vars)

train_ordinal_encoded = rank_hot_encode(train_ordinal, ordinal_vars)
test_ordinal_encoded = rank_hot_encode(test_ordinal, ordinal_vars)

In [14]:
all_categorical = train_categorical_dummied.join(train_ordinal_encoded)
all_categorical_test = test_categorical_dummied.join(test_ordinal_encoded)
print("# Columns for train data =", len(all_categorical.columns))
print("# Columns for test data =", len(all_categorical_test.columns))
all_categorical.head(3)

# Columns for train data = 798
# Columns for test data = 674


Electricity  Agricultural Household indicator_1  \
0            1                                   1   
1            0                                   0   
2            1                                   0   

   Agricultural Household indicator_2  Region_CAR  Region_Caraga  \
0                                   0           1              0   
1                                   0           0              0   
2                                   0           0              0   

   Region_I - Ilocos Region  Region_II - Cagayan Valley  \
0                         0                           0   
1                         0                           0   
2                         0                           0   

   Region_III - Central Luzon  Region_IVA - CALABARZON  Region_IVB - MIMAROPA  \
0                           0                        0                      0   
1                           0                        0                      0   
2                           1                        0                      0   

   Region_IX - Zasmboanga Peninsula  Region_NCR  Region_V - Bicol Region  \
0                                 0           0                        0   
1                                 0           0                        1   
2                                 0           0                        0   

   Region_VI - Western Visayas  Region_VII - Central Visayas  \
0                            0                             0   
1                            0                             0   
2                            0                             0   

   Region_VIII - Eastern Visayas  Region_X - Northern Mindanao  \
0                              0                             0   
1                              0                             0   
2                              0                             0   

   Region_XI - Davao Region  Region_XII - SOCCSKSARGEN  \
0                         0                          0   
1                         0                          0   
2                         0                          0   

   Main Source of Income_Other sources of Income  \
0                                              0   
1                                              1   
2                                              0   

   Main Source of Income_Wage/Salaries  Household Head Sex_Male  \
0                                    0                        1   
1                                    0                        1   
2                                    0                        1   

   Household Head Marital Status_Divorced/Separated  \
0                                                 0   
1                                                 0   
2                                                 0   

   Household Head Marital Status_Married  \
0                                      1   
1                                      1   
2                                      1   

   Household Head Marital Status_Single  \
0                                     0   
1                                     0   
2                                     0   

   Household Head Marital Status_Unknown  \
0                                      0   
1                                      0   
2                                      0   

   Household Head Marital Status_Widowed  \
0                                      0   
1                                      0   
2                                      0   

   Household Head Highest Grade Completed_Architecture and Building Programs  \
0                                                  0                           
1                                                  0                           
2                                                  0                           

   Household Head Highest Grade Completed_Arts Programs  \
0                                                  0      
1                                                

In [15]:
# Use sets to find common columns existing in train and test set
common_cols = list(set(all_categorical.columns) & set(all_categorical_test.columns))
common_cols.sort()
len(common_cols)

662

In [16]:
train_categorical_scaled = all_categorical[common_cols]
test_categorical_scaled = all_categorical_test[common_cols]
len(train_categorical_scaled.columns) == len(test_categorical_scaled.columns)

True

In [17]:
# Configure the Neural Network
nn = NeuralNetwork(len(train_categorical_scaled.columns))
nn.add_layer(64, "tanh").add_layer(1, "identity", bias = False)

In [43]:
# Train the Neural Network
nn.fit(train_categorical_scaled, train_y_scaled, eta = 0.0001, epochs = 10)

Inputs have been converted. Training starting now.
Epoch 0 - Training cost: 1.25896847601
Epoch 0 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 1 - Training cost: 0.574061872024
Epoch 1 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 2 - Training cost: 0.549838934116
Epoch 2 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 3 - Training cost: 0.523148574913
Epoch 3 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 4 - Training cost: 0.509509719549
Epoch 4 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 5 - Training cost: 0.500047353694
Epoch 5 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.

In [44]:
# Predict with the Neural Network against training data for metrics purposes
predicted_y_scaled = nn.predict(train_categorical_scaled)
predicted_y = yScaler.inverse_transform(predicted_y_scaled.reshape(predicted_y_scaled.shape[0],))
mean_squared_error(train_y_scaled, predicted_y_scaled)

0.47444298004387875

In [46]:
# Predict with the Neural Network against test data
predicted_y_scaled_test = nn.predict(test_categorical_scaled)
predicted_y_test = yScaler.inverse_transform(predicted_y_scaled_test.reshape(predicted_y_scaled_test.shape[0],))

### All Variables Neural Network

In [19]:
train_all_scaled = train_continuous_scaled.join(train_categorical_scaled)
test_all_scaled = test_continuous_scaled.join(test_categorical_scaled)
len(test_all_scaled.columns) == len(train_all_scaled.columns)

True

In [57]:
# Configure the Neural Network
nn = NeuralNetwork(len(train_all_scaled.columns))
nn.add_layer(64, "relu").add_layer(32, "relu").add_layer(16, "relu").add_layer(1, "identity", bias = False)

In [58]:
# Train the Neural Network
nn.fit(train_all_scaled, train_y_scaled, eta = 0.0001, epochs = 40, l2_value=5)

Inputs have been converted. Training starting now.
Epoch 0 	Training cost: 1.59648693987
Epoch 0 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 1 	Training cost: 0.49209630487
Epoch 1 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 2 	Training cost: 0.378840361465
Epoch 2 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 3 	Training cost: 0.350171362157
Epoch 3 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 4 	Training cost: 0.314112149124
Epoch 4 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epoch 5 	Training cost: 0.297819576303
Epoch 5 |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% 
Epo

KeyboardInterrupt: 

In [19]:
# Predict with the Neural Network against training data for metrics purposes
predicted_y_scaled = nn.predict(train_all_scaled)
predicted_y = yScaler.inverse_transform(predicted_y_scaled.reshape(predicted_y_scaled.shape[0],))
mean_squared_error(train_y_scaled, predicted_y_scaled)

0.18579753019916917

In [23]:
# Predict with the Neural Network against test data
predicted_y_scaled_test = nn.predict(test_all_scaled)
predicted_y_test = yScaler.inverse_transform(predicted_y_scaled_test.reshape(predicted_y_scaled_test.shape[0],))

### Any Features Neural Network

In [20]:
interact_categorical_df_train = dummyify(train_categorical[interact_nominal_vars], interact_nominal_vars)
interact_categorical_df_test = dummyify(test_categorical[interact_nominal_vars], interact_nominal_vars)

In [70]:
train_all_scaled['Household Head Ma']
train_categorical_dummied['Household Head Ma']

Total Food Expenditure  Bread and Cereals Expenditure  \
0                   -0.060411                       1.409052   
1                   -1.141515                      -0.785831   
2                    1.063654                       0.439412   
3                    0.462866                       1.202307   
4                   -0.455928                      -0.099810   
5                    0.446135                       0.087790   
6                   -0.736906                      -0.726846   
7                    0.882423                       0.405558   
8                   -0.615969                      -0.372415   
9                    1.523943                       0.477553   
10                   0.348851                      -0.031363   
11                  -0.797587                       0.229637   
12                  -1.269392                      -1.289130   
13                  -1.161348                      -1.064276   
14                  -0.290789                       0.365717   
15                  -0.309245                      -0.635411   
16                   0.637932                       1.657486   
17                  -1.040721                      -1.124370   
18                  -0.898536                      -0.526753   
19                   1.359579                       0.504681   
20                  -0.430744                      -0.776074   
21                  -0.956950                      -0.697944   
22                  -0.399725                      -0.823677   
23                  -0.458623                       0.128075   
24                  -0.205912                       0.720444   
25                  -0.243988                       0.522716   
26                  -0.774711                      -0.549002   
27                   0.102576                       0.180334   
28                   0.180474                       0.129997   
29                   0.510132                       0.516877   
...                       ...                            ...   
33205                0.380006                      -0.296355   
33206               -0.315410                      -0.659286   
33207               -0.302847                       0.654288   
33208               -0.670136                      -0.919695   
33209               -0.497746                      -0.318456   
33210               -0.059791                       1.044347   
33211               -0.464361                       0.582885   
33212               -0.038213                       0.397206   
33213                0.519962                       0.750971   
33214               -0.342203                       0.106270   
33215               -0.747220                      -0.601261   
33216               -1.253088                      -1.084233   
33217                1.014333                       3.509174   
33218               -0.535435                      -1.406362   
33219               -0.252635                       0.303923   
33220               -1.235000                      -1.009208   
33221                0.319033                       0.931254   
33222               -0.895085                      -0.562085   
33223               -0.978624                      -0.970845   
33224                0.742293                       0.077738   
33225               -1.349248                      -1.560109   
33226                0.268879                       0.726653   
33227               -0.812322                      -0.724185   
33228                2.023918                       1.095054   
33229                0.513777                       0.998814   
33230                1.010456                       0.183734   
33231               -1.002994                      -1.144845   
33232                0.082782                       0.797391   
33233               -0.505016                      -0.424157   
33234                0.036505                      -0.172840   

       Total Rice Expenditure  Meat Ex

In [22]:
interact_nominal_vars

['Agricultural Household indicator',
 'Main Source of Income',
 'Household Head Sex',
 'Household Head Marital Status',
 'Household Head Class of Worker',
 'Type of Building/House',
 'Tenure Status']

In [21]:
# Adds interation variables
train_all = transform_x(train_all_scaled, interact_categorical_df_train)
test_all = transform_x(test_all_scaled, interact_categorical_df_test)
print("# Columns for train all data =", len(train_all.columns))
print("# Columns for test all data =", len(test_all.columns))

KeyError: 'Household Head Marital Status_Unknown'

### Functions

In [9]:
def interact_all(df, interact_categorical_df):
    for continuous in interact_continuous_vars:
        for categorical in interact_categorical_df.columns:
            interation_name = "interatct_" + continuous + "_" + categorical
            df[interation_name] = df[continuous] * df[categorical]
    
    return df

In [10]:
def transform_x(df, interact_categorical_df):
    df = interact_all(df, interact_categorical_df)
    return df

In [11]:
def dummyify(df, 
             cols_to_dummy = []
            ):
    """
    DESCRIPTION:
        * Converts a categorical variable in a Pandas DataFrame to dummy/indicator variables.
          Drops one of the dummy columns to create our baseline for modeling. 
          Drops original column containing categorical variable.
        
    PARAMS:
        * df            --> Pandas DataFrame containing data.
        * col_to_dummy  --> The name of the categorical variable to convert to a dummy variable.
        * col_to_drop   --> The name of one of the dummy variable columns to drops. 
                            Defaults to the first value of col_to_dummy.
        
    RETURNS:
        Pandas DataFrame with the categorical variable converted to dummy variables.
    """
    
    if not cols_to_dummy:
        raise ValueError("Please provide column to dummy")
        
    for col in cols_to_dummy:
        dummies = pd.get_dummies( df[col] )
        
        new_cols = [col + '_' + str(old_col) for old_col in dummies.columns] # Have to do this for ordinal variables
        dummies.columns = new_cols 
        col_to_drop = dummies.columns[0]

        df = pd.concat( [df, dummies], axis=1 ).drop( [col_to_drop, col], axis=1 )

    return df

In [12]:
def rank_hot_encode(df, 
                    cols_to_encode = []
                   ):
    """
    DESCRIPTION:
        * Converts ordinal variables in a Pandas DataFrame to continuous variables.
          Drops one of the dummy columns to create our baseline for modeling. 
          Drops original column containing categorical variable.
        
    PARAMS:
        * df            --> Pandas DataFrame containing data.
        * col_to_dummy  --> The name of the ordinal variable to convert to a dummy variable.
        
    RETURNS:
        Pandas DataFrame with the categorical variable converted to dummy variables.
    """
    for col_to_encode in cols_to_encode:
        dummied = pd.get_dummies(df[col_to_encode], drop_first = True)
        encoded_values = dummied.columns
        
        for index in range(0, len(dummied)):
            row = dummied.loc[index]
            if(sum(row) == 0):
                continue
            for col in encoded_values:
                if(row[col] == 0):
                    row[col] = 1
                else:
                    break

        new_cols = [col_to_encode + '_' + str(old_col) for old_col in dummied.columns]
        dummied.columns = new_cols 
        
        df = pd.concat( [df, dummied], axis=1 ).drop( [col_to_encode], axis=1 )
    return df